In [3]:
import soccerdata as sd
import numpy as np
import pandas as pd

[12/10/24 10:38:40] INFO     No custom team name replacements found. You can configure these in       ]8;id=499909;file://f:\GitFiles\soccerdata\soccerdata\_config.py\_config.py]8;;\:]8;id=569453;file://f:\GitFiles\soccerdata\soccerdata\_config.py#90\90]8;;\
                             C:\Users\ADMIN\soccerdata\config\teamname_replacements.json.                          

                    INFO     No custom league dict found. You can configure additional leagues in    ]8;id=160912;file://f:\GitFiles\soccerdata\soccerdata\_config.py\_config.py]8;;\:]8;id=860020;file://f:\GitFiles\soccerdata\soccerdata\_config.py#196\196]8;;\
                             C:\Users\ADMIN\soccerdata\config\league_dict.json.                                    

In [38]:
elo = sd.ClubElo()

[12/10/24 11:06:48] INFO     Saving cached data to C:\Users\ADMIN\soccerdata\data\ClubElo            ]8;id=899064;file://f:\GitFiles\soccerdata\soccerdata\_common.py\_common.py]8;;\:]8;id=753089;file://f:\GitFiles\soccerdata\soccerdata\_common.py#263\263]8;;\

In [ ]:
elo_ = elo.read_by_date()
elo_.to_csv("elo.csv")

In [61]:
mh = sd.MatchHistory(leagues="ENG-Premier League", seasons=[f'{i}/{i+1}' for i in range(2010, 2023)])
mh_matches = mh.read_games()
mh_matches.to_csv("mh_matches.csv")

[12/10/24 11:32:11] INFO     Saving cached data to C:\Users\ADMIN\soccerdata\data\MatchHistory       ]8;id=216497;file://f:\GitFiles\soccerdata\soccerdata\_common.py\_common.py]8;;\:]8;id=959054;file://f:\GitFiles\soccerdata\soccerdata\_common.py#263\263]8;;\

In [ ]:
understat = sd.Understat(leagues="ENG-Premier League", seasons=[f'{i}/{i+1}' for i in range(2014, 2023)])
understat_matches = understat.read_team_match_stats()
understat_matches.to_csv("understat_matches.csv")


In [ ]:
understat_players = understat.read_player_match_stats()
understat_players.to_csv("understat_players.csv")

# UNDERSTAT DATA

In [ ]:
understat_matches = pd.read_csv("understat_matches.csv")
understat_players = pd.read_csv("understat_players.csv")
understat_players['rating'] = (
    understat_players['goals'] * 4 +               # Điểm cao cho bàn thắng
    understat_players['assists'] * 3 +            # Điểm cho kiến tạo
    understat_players['key_passes'] * 2 +         # Điểm cho đường chuyền quan trọng
    understat_players['minutes'] / 90 -           # Thời gian thi đấu (chia cho 90 phút)
    understat_players['yellow_cards'] * 1 -       # Trừ điểm vì thẻ vàng
    understat_players['red_cards'] * 3            # Trừ điểm nặng hơn vì thẻ đỏ
)

In [ ]:
# Tính rating trung bình của từng đội trong từng trận
team_avg_rating_per_game = (
    understat_players.groupby(['game_id', 'team_id'])['rating']
    .mean()
    .reset_index()
)
# Tạo các cột trống trong bảng understat_matches
understat_matches['home_rating'] = None
understat_matches['away_rating'] = None

# Chuyển team_avg_rating_per_game thành từ điển để tra cứu nhanh
rating_lookup = team_avg_rating_per_game.set_index(['game_id', 'team_id'])['rating'].to_dict()

# Duyệt từng dòng trong bảng understat_matches
for idx, row in understat_matches.iterrows():
    game_id = row['game_id']
    home_team_id = row['home_team_id']
    away_team_id = row['away_team_id']

    # Lấy rating của đội nhà và đội khách từ từ điển lookup
    home_rating = rating_lookup.get((game_id, home_team_id), None)
    away_rating = rating_lookup.get((game_id, away_team_id), None)

    # Gán rating vào bảng understat_matches
    understat_matches.at[idx, 'home_rating'] = home_rating
    understat_matches.at[idx, 'away_rating'] = away_rating

# Chuyển các cột rating từ None thành float để dễ xử lý
understat_matches['home_rating'] = understat_matches['home_rating'].astype(float)
understat_matches['away_rating'] = understat_matches['away_rating'].astype(float)

# Kiểm tra kết quả
understat_matches.head()

league  season                                  game  \
0  ENG-Premier League    1415     2014-08-16 Arsenal-Crystal Palace   
1  ENG-Premier League    1415          2014-08-16 Leicester-Everton   
2  ENG-Premier League    1415  2014-08-16 Manchester United-Swansea   
3  ENG-Premier League    1415   2014-08-16 Queens Park Rangers-Hull   
4  ENG-Premier League    1415          2014-08-16 Stoke-Aston Villa   

   league_id  season_id  game_id                 date  home_team_id  \
0          1       2014     4755  2014-08-16 17:30:00            83   
1          1       2014     4750  2014-08-16 15:00:00            75   
2          1       2014     4749  2014-08-16 12:45:00            89   
3          1       2014     4751  2014-08-16 15:00:00           202   
4          1       2014     4752  2014-08-16 15:00:00            85   

   away_team_id            home_team  ... home_points home_expected_points  \
0            78              Arsenal  ...           3               2.7946   
1            72            Leicester  ...           1               1.9461   
2            84    Manchester United  ...           0               2.2359   
3            91  Queens Park Rangers  ...           0               2.0149   
4            71                Stoke  ...           0               0.8041   

  home_goals   home_xg  home_np_xg  home_np_xg_difference  home_ppda  \
0          2  1.554110    1.554110               1.395959   2.933333   
1          2  1.278300    1.278300               0.665027  14.480000   
2          1  1.166350    1.166350               0.888274  10.120000   
3          0  1.900670    1.126890               0.009320  12.823529   
4          0  0.423368    0.423368              -0.486406   4.125000   

   home_deep_completions  home_rating  away_rating  
0                      9     3.000000     1.357937  
1                      1     2.142857     2.538462  
2                      8     2.500000     2.214286  
3                      1     2.714286     2.428571  
4                      3     2.384615     1.692308  

[5 rows x 31 columns]

In [ ]:
columns_to_drop = ['league','season','game','league_id','season_id','game_id','date','home_team','away_team','away_team_code','home_team_code',
                   'away_goals','home_goals','home_points','away_np_xg','home_np_xg','away_np_xg_difference','home_np_xg_difference',]
understat_matches.rename(columns={'away_points':'result'}, inplace=True)
understat_matches = understat_matches.drop(columns=columns_to_drop)
understat_matches.to_csv("ditcu.csv")

In [ ]:
understat_matches.head()

home_team_id  away_team_id  result  away_expected_points   away_xg  \
0            83            78       0                0.1114  0.158151   
1            75            72       1                0.7617  0.613273   
2            89            84       3                0.4839  0.278076   
3           202            91       3                0.7402  1.117570   
4            85            71       3                1.8322  0.909774   

   away_ppda  away_deep_completions  home_expected_points   home_xg  \
0  14.172414                      0                2.7946  1.554110   
1  11.687500                     15                1.9461  1.278300   
2  17.947368                      2                2.2359  1.166350   
3  10.285714                      5                2.0149  1.900670   
4  14.043478                      4                0.8041  0.423368   

   home_ppda  home_deep_completions  home_rating  away_rating  
0   2.933333                      9     3.000000     1.357937  
1  14.480000                      1     2.142857     2.538462  
2  10.120000                      8     2.500000     2.214286  
3  12.823529                      1     2.714286     2.428571  
4   4.125000                      3     2.384615     1.692308

# MATCH HISTORY DATA

In [62]:
data = pd.read_csv('mh_matches.csv')
data['Hodds'] = np.mean(data[['B365H','BWH','IWH','LBH','PSH','WHH','SJH','VCH']],axis=1)
data['Dodds'] = np.mean(data[['B365D','BWD','IWD','LBD','PSD','WHD','SJD','VCD']],axis=1)
data['Aodds'] = np.mean(data[['B365A','BWA','IWA','LBA','PSA','WHA','SJA','VCA']],axis=1)
use_col = ['date','home_team','away_team','FTHG','FTAG','FTR','HTHG','HTAG','HTR','HS','AS','HST','AST',
            'HC','AC','HF','AF','HY','AY','HR','AR','Hodds','Dodds','Aodds']
data = data[use_col]

In [ ]:
acc_hist = {'home_wins' : [], 'home_draws' : [], 'home_losses' : [], 'home_goals' : [], 'home_oppos_goals' : [],
            'home_shots' : [], 'home_oppos_shots' : [], 'home_shotontarget' : [], 'home_oppos_shotontarget' : [],
            'away_wins' : [], 'away_draws' : [], 'away_losses' : [], 'away_goals' : [], 'away_oppos_goals' : [],
            'away_shots' : [], 'away_oppos_shots' : [], 'away_shotontarget' : [], 'away_oppos_shotontarget' : [],
            'home_oppos_wins' : [], 'home_oppos_draws' : [], 'home_oppos_losses' : [],
            'home_fouls' : [], 'home_yellowcards' : [], 'home_redcards' : [], 'home_cornerkicks' : [],
            'home_oppos_cornerkicks' : [], 'home_oppos_fouls' : [], 'home_oppos_yellowcards' : [], 'home_oppos_redcards' : [],
            'away_fouls' : [], 'away_yellowcards' : [], 'away_redcards' : [], 'away_cornerkicks' : [],
            'away_oppos_cornerkicks' : [],'away_oppos_fouls' : [], 'away_oppos_yellowcards' : [], 'away_oppos_redcards' : [],
            
            'wins' : [], 'draws' : [], 'losses' : [], 
            'oppos_wins' : [], 'oppos_draws' : [], 'oppos_losses' : [],

            'goals' : [], 'shots' : [], 'shotontarget' : [], 
            'cornerkicks' : [], 'fouls' : [], 'yellowcards' : [], 'redcards' : [],  
            'oppos_goals' : [], 'oppos_shots' : [], 'oppos_shotontarget' : [], 
            'oppos_cornerkicks' : [], 'oppos_fouls' : [], 'oppos_yellowcards' : [], 'oppos_redcards' : []
            }

In [64]:
import functools
def conjunction(*conditions):
    return functools.reduce(np.logical_and, conditions)

def union(*conditions):
    return functools.reduce(np.logical_or, conditions)

lookback_opp_matches = 3
lookback_matches = 5

In [65]:
for row in data.iterrows() :
    hometeam = row[1]['home_team']
    awayteam = row[1]['away_team']
    date = row[1]['date']

    # filter matches with same playing teams
    temp1 = data[conjunction(data['home_team']==hometeam, data['away_team']==awayteam)]
    temp2 = data[conjunction(data['home_team']==awayteam, data['away_team']==hometeam)]
    temp = pd.concat([temp1, temp2], axis=0)
    history = temp[temp['date']<date].sort_values(by='date').tail(lookback_opp_matches)
    # if opponent history is too short, continue
    if len(history) < lookback_opp_matches :
        for key in list(acc_hist.keys()) :
            acc_hist[key].append(np.nan)
        continue

    # compute average number of goals scored against opponent in the past N matches with the opponent
    home = history[history['home_team'] == hometeam]
    away = history[history['away_team'] == hometeam]
    home_sum = np.sum(home[['FTHG','FTAG','HS','AS','HST','AST','HC','AC','HF','AF','HY','AY','HR','AR']])
    away_sum = np.sum(away[['FTHG','FTAG','HS','AS','HST','AST','HC','AC','HF','AF','HY','AY','HR','AR']])


    # filter recent N matches of both home and away
    home = data[union(data['home_team']==hometeam, data['away_team']==hometeam)]
    home = home[home['date']<date].sort_values(by='date').tail(lookback_matches)
    away = data[union(data['home_team']==awayteam, data['away_team']==awayteam)]
    away = away[away['date']<date].sort_values(by='date').tail(lookback_matches)

    # if match history is too short, continue
    if len(home) < lookback_matches or len(away) < lookback_matches :
        for key in list(acc_hist.keys()) :
            acc_hist[key].append(np.nan)
        continue

    home_home_sum = np.sum(home[home['home_team']==hometeam][['FTHG','HS','HST','HC','HF','HY','HR']])
    home_away_sum = np.sum(home[home['away_team']==hometeam][['FTAG','AS','AST','AC','AF','AY','AR']])
    away_home_sum = np.sum(away[away['home_team']==awayteam][['FTHG','HS','HST','HC','HF','HY','HR']])
    away_away_sum = np.sum(away[away['away_team']==awayteam][['FTAG','AS','AST','AC','AF','AY','AR']])

    # append computation results to dictionary
    acc_hist['home_oppos_goals'].append((home_sum['FTHG'] + away_sum['FTAG']) / lookback_opp_matches)
    acc_hist['away_oppos_goals'].append((home_sum['FTAG'] + away_sum['FTHG']) / lookback_opp_matches)
    acc_hist['home_oppos_shots'].append((home_sum['HS'] + away_sum['AS']) / lookback_opp_matches)
    acc_hist['away_oppos_shots'].append((home_sum['AS'] + away_sum['HS']) / lookback_opp_matches)
    acc_hist['home_oppos_shotontarget'].append((home_sum['HST'] + away_sum['AST']) / lookback_opp_matches)
    acc_hist['away_oppos_shotontarget'].append((home_sum['AST'] + away_sum['HST']) / lookback_opp_matches)
    acc_hist['home_oppos_cornerkicks'].append((home_sum['HC'] + away_sum['AC']) / lookback_opp_matches)
    acc_hist['away_oppos_cornerkicks'].append((home_sum['AC'] + away_sum['HC']) / lookback_opp_matches)
    acc_hist['home_oppos_fouls'].append((home_sum['HF'] + away_sum['AF']) / lookback_opp_matches)
    acc_hist['away_oppos_fouls'].append((home_sum['AF'] + away_sum['HF']) / lookback_opp_matches)
    acc_hist['home_oppos_yellowcards'].append((home_sum['HY'] + away_sum['AY']) / lookback_opp_matches)
    acc_hist['away_oppos_yellowcards'].append((home_sum['AY'] + away_sum['HY']) / lookback_opp_matches)
    acc_hist['home_oppos_redcards'].append((home_sum['HR'] + away_sum['AR']) / lookback_opp_matches)
    acc_hist['away_oppos_redcards'].append((home_sum['AR'] + away_sum['HR']) / lookback_opp_matches)

    acc_hist['home_goals'].append((home_home_sum['FTHG'] + home_away_sum['FTAG']) / lookback_matches)
    acc_hist['away_goals'].append((away_home_sum['FTHG'] + away_away_sum['FTAG']) / lookback_matches)
    acc_hist['home_shots'].append((home_home_sum['HS'] + home_away_sum['AS']) / lookback_matches)
    acc_hist['away_shots'].append((away_home_sum['HS'] + away_away_sum['AS']) / lookback_matches)
    acc_hist['home_shotontarget'].append((home_home_sum['HST'] + home_away_sum['AST']) / lookback_matches)
    acc_hist['away_shotontarget'].append((away_home_sum['HST'] + away_away_sum['AST']) / lookback_matches)
    acc_hist['home_cornerkicks'].append((home_home_sum['HC'] + home_away_sum['AC']) / lookback_matches)
    acc_hist['away_cornerkicks'].append((away_home_sum['HC'] + away_away_sum['AC']) / lookback_matches)
    acc_hist['home_fouls'].append((home_home_sum['HF'] + home_away_sum['AF']) / lookback_matches)
    acc_hist['away_fouls'].append((away_home_sum['HF'] + away_away_sum['AF']) / lookback_matches)
    acc_hist['home_yellowcards'].append((home_home_sum['HY'] + home_away_sum['AY']) / lookback_matches)
    acc_hist['away_yellowcards'].append((away_home_sum['HY'] + away_away_sum['AY']) / lookback_matches)
    acc_hist['home_redcards'].append((home_home_sum['HR'] + home_away_sum['AR']) / lookback_matches)
    acc_hist['away_redcards'].append((away_home_sum['HR'] + away_away_sum['AR']) / lookback_matches)


    # count ratio of wins / draws / losses in the past N matches of Home vs Away
    res = []
    for r in history.iterrows() :
        if r[1]['home_team'] == hometeam :
            res.append(r[1]['FTR'])
        else :
            if r[1]['FTR'] == 'A' :
                res.append('H')
            elif r[1]['FTR'] == 'H' :
                res.append('A')
            else :
                res.append('D')
    acc_hist['home_oppos_wins'].append(res.count('H') / lookback_opp_matches)
    acc_hist['home_oppos_draws'].append(res.count('D') / lookback_opp_matches)
    acc_hist['home_oppos_losses'].append(res.count('A') / lookback_opp_matches)


    # count ratio of wins / draws / losses in the past N matches
    res = []
    for r in home.iterrows() :
        if r[1]['home_team'] == hometeam :
            res.append(r[1]['FTR'])
        else :
            if r[1]['FTR'] == 'A' :
                res.append('H')
            elif r[1]['FTR'] == 'H' :
                res.append('A')
            else :
                res.append('D')
    acc_hist['home_wins'].append(res.count('H') / lookback_matches)
    acc_hist['home_draws'].append(res.count('D') / lookback_matches)
    acc_hist['home_losses'].append(res.count('A') / lookback_matches)

    res = []
    for r in away.iterrows() :
        if r[1]['home_team'] == awayteam :
            res.append(r[1]['FTR'])
        else :
            if r[1]['FTR'] == 'A' :
                res.append('H')
            elif r[1]['FTR'] == 'H' :
                res.append('A')
            else :
                res.append('D')
    acc_hist['away_wins'].append(res.count('H') / lookback_matches)
    acc_hist['away_draws'].append(res.count('D') / lookback_matches)
    acc_hist['away_losses'].append(res.count('A') / lookback_matches)

    acc_hist['wins'].append(acc_hist['home_wins'][-1] - acc_hist['away_wins'][-1])
    acc_hist['draws'].append(acc_hist['home_draws'][-1] - acc_hist['away_draws'][-1])
    acc_hist['losses'].append(acc_hist['home_losses'][-1] - acc_hist['away_losses'][-1])

    acc_hist['oppos_wins'].append(acc_hist['home_oppos_wins'][-1])
    acc_hist['oppos_draws'].append(acc_hist['home_oppos_draws'][-1])
    acc_hist['oppos_losses'].append(acc_hist['home_oppos_losses'][-1])

    acc_hist['goals'].append(acc_hist['home_goals'][-1] - acc_hist['away_goals'][-1])
    acc_hist['shots'].append(acc_hist['home_shots'][-1] - acc_hist['away_shots'][-1])
    acc_hist['shotontarget'].append(acc_hist['home_shotontarget'][-1] - acc_hist['away_shotontarget'][-1])
    acc_hist['cornerkicks'].append(acc_hist['home_cornerkicks'][-1] - acc_hist['away_cornerkicks'][-1])
    acc_hist['fouls'].append(acc_hist['home_fouls'][-1] - acc_hist['away_fouls'][-1])
    acc_hist['yellowcards'].append(acc_hist['home_yellowcards'][-1] - acc_hist['away_yellowcards'][-1])
    acc_hist['redcards'].append(acc_hist['home_redcards'][-1] - acc_hist['away_redcards'][-1])

    acc_hist['oppos_goals'].append(acc_hist['home_oppos_goals'][-1] - acc_hist['away_oppos_goals'][-1])
    acc_hist['oppos_shots'].append(acc_hist['home_oppos_shots'][-1] - acc_hist['away_oppos_shots'][-1])
    acc_hist['oppos_shotontarget'].append(acc_hist['home_oppos_shotontarget'][-1] - acc_hist['away_oppos_shotontarget'][-1])
    acc_hist['oppos_cornerkicks'].append(acc_hist['home_oppos_cornerkicks'][-1] - acc_hist['away_oppos_cornerkicks'][-1])
    acc_hist['oppos_fouls'].append(acc_hist['home_oppos_fouls'][-1] - acc_hist['away_oppos_fouls'][-1])
    acc_hist['oppos_yellowcards'].append(acc_hist['home_oppos_yellowcards'][-1] - acc_hist['away_oppos_yellowcards'][-1])
    acc_hist['oppos_redcards'].append(acc_hist['home_oppos_redcards'][-1] - acc_hist['away_oppos_redcards'][-1])

f:\Apps\miniconda3\Lib\site-packages\numpy\core\fromnumeric.py:86: FutureWarning: The behavior of DataFrame.sum with axis=None is deprecated, in a future version this will reduce over both axes and return a scalar. To retain the old behavior, pass axis=0 (or do not pass axis)
  return reduction(axis=axis, out=out, **passkwargs)
f:\Apps\miniconda3\Lib\site-packages\numpy\core\fromnumeric.py:86: FutureWarning: The behavior of DataFrame.sum with axis=None is deprecated, in a future version this will reduce over both axes and return a scalar. To retain the old behavior, pass axis=0 (or do not pass axis)
  return reduction(axis=axis, out=out, **passkwargs)
f:\Apps\miniconda3\Lib\site-packages\numpy\core\fromnumeric.py:86: FutureWarning: The behavior of DataFrame.sum with axis=None is deprecated, in a future version this will reduce over both axes and return a scalar. To retain the old behavior, pass axis=0 (or do not pass axis)
  return reduction(axis=axis, out=out, **passkwargs)
f:\Apps\mi

In [66]:
acc_hist = pd.DataFrame(acc_hist)

In [99]:
acc_hist_from_2014 = acc_hist[-3420:].reset_index(drop=True)
acc_hist_from_2014

home_wins  home_draws  home_losses  home_goals  home_oppos_goals  \
0           NaN         NaN          NaN         NaN               NaN   
1           NaN         NaN          NaN         NaN               NaN   
2           0.4         0.2          0.4         1.6          2.666667   
3           NaN         NaN          NaN         NaN               NaN   
4           0.6         0.2          0.2         1.6          2.333333   
...         ...         ...          ...         ...               ...   
3415        0.2         0.4          0.4         1.8          0.666667   
3416        0.0         0.4          0.6         1.2          1.333333   
3417        0.0         0.6          0.4         1.2          1.666667   
3418        0.6         0.0          0.4         1.4          1.666667   
3419        0.0         0.0          1.0         1.0          0.666667   

      home_shots  home_oppos_shots  home_shotontarget  \
0            NaN               NaN                NaN   
1            NaN               NaN                NaN   
2           15.4         15.666667                4.8   
3            NaN               NaN                NaN   
4           15.8          9.333333                4.6   
...          ...               ...                ...   
3415        14.4         14.000000                5.0   
3416        10.6         16.333333                3.6   
3417        10.6          9.000000                4.6   
3418        20.0         14.000000                6.4   
3419         8.8          6.666667                2.4   

      home_oppos_shotontarget  away_wins  ...  fouls  yellowcards  redcards  \
0                         NaN        NaN  ...    NaN          NaN       NaN   
1                         NaN        NaN  ...    NaN          NaN       NaN   
2                    7.000000        0.6  ...   -0.4          0.6      -0.2   
3                         NaN        NaN  ...    NaN          NaN       NaN   
4                    3.000000        0.2  ...   -1.2          0.0       0.2   
...                       ...        ...  ...    ...          ...       ...   
3415                 4.333333        0.4  ...    1.0          0.4       0.0   
3416                 5.000000        0.2  ...    3.4          0.6       0.2   
3417                 3.000000        0.4  ...    3.2          1.4       0.0   
3418                 6.666667        0.4  ...   -0.8          1.2       0.0   
3419                 3.333333        0.8  ...   -3.8          0.0       0.0   

      oppos_goals  oppos_shots  oppos_shotontarget  oppos_cornerkicks  \
0             NaN          NaN                 NaN                NaN   
1             NaN          NaN                 NaN                NaN   
2        2.000000     4.000000            3.666667          -1.000000   
3             NaN          NaN                 NaN                NaN   
4        0.666667    -3.000000           -2.000000          -0.333333   
...           ...          ...                 ...                ...   
3415    -2.333333     0.000000           -3.000000          -0.333333   
3416    -2.000000     2.333333           -2.666667          -2.000000   
3417    -0.333333    -4.000000           -2.333333          -4.666667   
3418     0.666667     2.666667            1.000000           1.333333   
3419    -2.333333   -13.000000           -2.666667          -4.000000   

      oppos_fouls  oppos_yellowcards  oppos_redcards  
0             NaN                NaN             NaN  
1             NaN                NaN             NaN  
2       -1.666667           0.000000        0.000000  
3             NaN                NaN             NaN  
4       -1.666667          -2.000000        0.000000  
...           ...                ...             ...  
3415     2.333333           1.000000        0.000000  
3416     1.666667           1.666667        0.333333  
3417     0.000000          -0.666667        0.333333  
3418     0.000000          -1.000000        0.000000  
3

In [100]:
acc_hist_from_2014.drop(columns=[
            'home_wins', 'home_draws', 'home_losses', 
            'home_goals', 'home_oppos_goals', 
            'home_shots', 'home_oppos_shots', 
            'home_shotontarget', 'home_oppos_shotontarget', 
            'away_wins', 'away_draws', 'away_losses', 
            'away_goals', 'away_oppos_goals', 
            'away_shots', 'away_oppos_shots', 
            'away_shotontarget', 'away_oppos_shotontarget', 
            'home_oppos_wins', 'home_oppos_draws', 'home_oppos_losses', 
            'home_fouls', 'home_yellowcards', 'home_redcards', 
            'home_cornerkicks', 'home_oppos_cornerkicks', 
            'home_oppos_fouls', 'home_oppos_yellowcards', 'home_oppos_redcards', 
            'away_fouls', 'away_yellowcards', 'away_redcards', 
            'away_cornerkicks','away_oppos_cornerkicks', 
            'away_oppos_fouls', 'away_oppos_yellowcards', 'away_oppos_redcards'
], inplace=True)

In [105]:
acc_hist_from_2014.to_csv('acc_hist_from_2014.csv')

In [102]:
final_data = pd.concat([understat_matches, acc_hist_from_2014], axis=1)

In [103]:
final_data.to_csv('final_data.csv')

In [107]:
final_data.isnull().sum()

home_team_id               0
away_team_id               0
result                     0
away_expected_points       0
away_xg                    0
away_ppda                  0
away_deep_completions      0
home_expected_points       0
home_xg                    0
home_ppda                  0
home_deep_completions      0
home_rating                0
away_rating                0
wins                     707
draws                    707
losses                   707
oppos_wins               707
oppos_draws              707
oppos_losses             707
goals                    707
shots                    707
shotontarget             707
cornerkicks              707
fouls                    707
yellowcards              707
redcards                 707
oppos_goals              707
oppos_shots              707
oppos_shotontarget       707
oppos_cornerkicks        707
oppos_fouls              707
oppos_yellowcards        707
oppos_redcards           707
dtype: int64

# SPLIT TEST VAL TRAIN

In [114]:
test = final_data[-380:].reset_index(drop=True)
val = final_data[-760:-380].reset_index(drop=True)
train = final_data[:-760].reset_index(drop=True)

In [115]:
test.dropna(inplace=True)
val.dropna(inplace=True)
train.dropna(inplace=True)
test.to_csv('cleaned/test.csv', index=False)
val.to_csv('cleaned/val.csv', index=False)
train.to_csv('cleaned/train.csv', index=False)

In [116]:
test

home_team_id  away_team_id  result  away_expected_points   away_xg  \
0              78            83       3                1.5584  1.436010   
1              73            71       0                1.1567  0.488895   
2              72            80       3                2.4766  1.923150   
3             228            87       1                2.2059  2.341110   
4             245           229       0                1.5274  1.101190   
..            ...           ...     ...                   ...       ...   
375            72            73       0                0.6810  0.432084   
376           245            82       3                2.0183  2.033150   
377            75            81       0                0.6372  0.970352   
378            89           228       0                0.8456  1.881670   
379            74            87       1                2.7285  4.003450   

     away_ppda  away_deep_completions  home_expected_points   home_xg  \
0    12.678571                     13                1.1504  1.206370   
1     6.608696                     11                1.4036  0.588341   
2     6.192308                      7                0.3517  0.541983   
3     6.333333                     11                0.5808  1.268220   
4    10.647059                      9                1.1560  0.889170   
..         ...                    ...                   ...       ...   
375   7.450000                      4                2.0160  1.129330   
376  13.733333                      5                0.7658  1.191510   
377  15.650000                      8                2.1522  2.030130   
378  16.875000                      8                1.9385  2.747660   
379   3.750000                     20                0.1953  1.339640   

     home_ppda  ...  fouls  yellowcards  redcards  oppos_goals  oppos_shots  \
0    10.250000  ...    1.8          0.6      -0.2     0.333333    -2.666667   
1    11.680000  ...   -0.2          0.8       0.0     1.000000    -2.000000   
2    12.000000  ...   -2.2         -1.0       0.4    -0.333333   -12.666667   
3    18.473684  ...    2.8          0.2       0.0     0.000000    -5.666667   
4     9.285714  ...    8.0          0.6       0.4     0.000000     4.666667   
..         ...  ...    ...          ...       ...          ...          ...   
375  13.884615  ...    1.0          0.4       0.0    -2.333333     0.000000   
376   8.689655  ...    3.4          0.6       0.2    -2.000000     2.333333   
377  14.666667  ...    3.2          1.4       0.0    -0.333333    -4.000000   
378   7.677419  ...   -0.8          1.2       0.0     0.666667     2.666667   
379  31.090909  ...   -3.8          0.0       0.0    -2.333333   -13.000000   

     oppos_shotontarget  oppos_cornerkicks  oppos_fouls  oppos_yellowcards  \
0              1.666667          -1.666667    -2.333333          -0.333333   
1              0.000000          -2.333333    -1.333333           0.000000   
2             -5.333333          -5.000000    -0.666667           0.666667   
3             -1.666667          -5.333333     2.000000           1.333333   
4              0.000000           2.666667    -1.000000           0.333333   
..                  ...                ...          ...                ...   
375           -3.000000          -0.333333     2.333333           1.000000   
376           -2.666667          -2.000000     1.666667           1.666667   
377           -2.333333          -4.666667     0.000000          -0.666667   
378            1.000000           1.333333     0.000000          -1.000000   
379           -2.666667          -4.000000     2.333333           1.666667   

     oppos_redcards  
0          0.000000  
1          0.333333  
2          0.000000  
3          0.000000  
4         -0.333333  
..              ...  
375        0.000000  
376        0.333333  
377        0.333333  
378        0.000000  
379        0.000000  

[318 rows x 33 columns]

In [117]:
val

home_team_id  away_team_id  result  away_expected_points   away_xg  \
1              92           220       3                1.2564  1.685300   
2              80            78       0                0.5141  0.321701   
3              72            74       0                0.2455  0.580601   
4              75           229       0                1.9451  1.327140   
6              79            87       3                1.7064  1.787280   
..            ...           ...     ...                   ...       ...   
375            78            89       0                1.7546  0.782005   
376            75            74       0                0.1395  1.051410   
377            87           229       0                0.2766  1.117080   
378            88            71       0                0.0308  0.247841   
379            79            82       3                2.9626  3.815000   

     away_ppda  away_deep_completions  home_expected_points   home_xg  \
1     7.933333                      7                1.4559  1.795480   
2    71.000000                      3                2.2037  1.187090   
3     5.592593                      6                2.6311  2.388630   
4    20.263158                      7                0.7799  0.668082   
6    11.580645                     13                1.0335  1.333300   
..         ...                    ...                   ...       ...   
375   5.888889                      5                0.8426  0.354618   
376  12.600000                      5                2.7888  3.420580   
377  33.363636                      4                2.6115  3.193850   
378  23.500000                      1                2.9495  3.320900   
379  17.071429                     12                0.0217  0.310789   

     home_ppda  ...  fouls  yellowcards  redcards  oppos_goals  oppos_shots  \
1    17.888889  ...   -3.4         -0.6      -0.4    -0.333333    -2.000000   
2     6.595238  ...    0.0         -1.0       0.2     2.666667    12.000000   
3     6.869565  ...   -0.6         -0.4       0.0    -0.333333    -4.666667   
4    11.500000  ...    0.6         -0.6       0.0     0.333333    -1.000000   
6    25.666667  ...   -1.4          1.2       0.4    -1.666667    -7.333333   
..         ...  ...    ...          ...       ...          ...          ...   
375  15.500000  ...    4.4          0.8       0.0     0.333333    -3.333333   
376  12.437500  ...    0.0          0.4       0.0     0.666667     8.666667   
377  10.280000  ...    3.6          0.4       0.0     2.000000     6.000000   
378   7.294118  ...   -5.2         -0.2       0.0     1.333333    10.000000   
379  16.791667  ...   -1.4         -0.8       0.0    -1.333333    -6.333333   

     oppos_shotontarget  oppos_cornerkicks  oppos_fouls  oppos_yellowcards  \
1              0.333333          -0.666667    -2.666667           1.333333   
2              5.666667           4.333333     2.666667           0.000000   
3             -1.333333          -2.333333     1.000000          -0.333333   
4              1.000000          -3.333333     1.666667           0.333333   
6             -3.000000          -4.666667    -3.333333           0.000000   
..                  ...                ...          ...                ...   
375            0.333333          -3.666667    -6.333333           0.000000   
376            2.333333           3.000000     0.000000           0.333333   
377            2.000000           1.000000    -3.333333          -0.333333   
378            3.000000          10.333333     0.000000          -0.333333   
379           -4.000000          -2.666667    -3.333333           0.666667   

     oppos_redcards  
1          0.000000  
2          0.000000  
3          0.333333  
4          0.333333  
6          0.000000  
..              ...  
375        0.000000  
376       -0.333333  
377        0.000000  
378        0.000000  
379        0.000000  

[320 rows x 33 columns]

In [118]:
train

home_team_id  away_team_id  result  away_expected_points   away_xg  \
2               89            84       3                0.4839  0.278076   
4               85            71       3                1.8322  0.909774   
5               76            77       1                0.6966  0.991901   
6               81            82       3                0.7136  1.017060   
7               87            74       0                1.5269  1.552480   
...            ...           ...     ...                   ...       ...   
2655            87            78       0                0.3992  0.772317   
2656            88            72       0                0.3316  1.072580   
2657           238            92       0                1.4201  0.558508   
2658            81            74       0                0.9417  1.351790   
2659           229            89       3                2.4249  2.052290   

      away_ppda  away_deep_completions  home_expected_points   home_xg  \
2     17.947368                      2                2.2359  1.166350   
4     14.043478                      4                0.8041  0.423368   
5     13.687500                      3                2.0358  1.683430   
6     10.956522                      3                2.0216  1.853100   
7     11.138889                      9                1.1777  1.331920   
...         ...                    ...                   ...       ...   
2655  16.750000                      1                2.4278  2.203480   
2656  19.115385                      3                2.5201  2.883550   
2657   9.352941                     10                1.1129  0.420006   
2658   6.166667                     10                1.8246  1.983440   
2659  29.181818                      6                0.4026  0.701256   

      home_ppda  ...  fouls  yellowcards  redcards  oppos_goals  oppos_shots  \
2     10.120000  ...   -0.4          0.6      -0.2     2.000000     4.000000   
4      4.125000  ...   -1.2          0.0       0.2     0.666667    -3.000000   
5      5.935484  ...   -4.2         -1.4       0.0     0.666667     5.333333   
6     11.250000  ...   -0.6         -0.6      -0.2     1.333333    -2.333333   
7     11.333333  ...   -1.6          0.2       0.2     0.000000    -4.000000   
...         ...  ...    ...          ...       ...          ...          ...   
2655   5.391304  ...   -1.6         -1.8       0.0     4.000000     7.666667   
2656  10.000000  ...   -0.2          1.2       0.4     1.666667    10.000000   
2657   8.653846  ...    1.8          1.0       0.0     0.666667     3.333333   
2658  17.764706  ...   -2.6          0.4       0.0     1.000000     1.333333   
2659   8.250000  ...   -1.0         -0.4       0.0    -0.333333    -2.000000   

      oppos_shotontarget  oppos_cornerkicks  oppos_fouls  oppos_yellowcards  \
2               3.666667          -1.000000    -1.666667           0.000000   
4              -2.000000          -0.333333    -1.666667          -2.000000   
5               1.333333          -2.000000     0.333333          -0.333333   
6              -1.333333          -0.333333     1.000000          -0.333333   
7              -1.666667           0.333333    -2.333333           0.333333   
...                  ...                ...          ...                ...   
2655            3.333333           1.333333     2.333333           0.000000   
2656            3.666667           1.333333     1.333333          -1.666667   
2657            1.666667           3.000000     2.000000           0.000000   
2658            2.333333          -1.000000     0.333333           0.000000   
2659            0.000000           0.000000     2.000000          -0.333333   

      oppos_redcards  
2           0.000000  
4           0.000000  
5           0.000000  
6          -0.333333  
7           0.000000  
...              ...  
2655        0.000000  
2656        0.000000  
2657        0.000000  
2658        0.000000  
2659        0.000000  

[2075 rows x 33 c